# Example image analysis with OMERO and python

Adapted from:
[https://github.com/rmassei/2024-jn-omero-pipeline/blob/main/02_jupyter_notebook/02_solution/JN-pipeline_solution.ipynb](https://github.com/rmassei/2024-jn-omero-pipeline/blob/main/02_jupyter_notebook/02_solution/JN-pipeline_solution.ipynb)

In [ ]:
import getpass

import ezomero
import omero
import omero_rois

import pandas as pd
import omero
import tifffile
import numpy as np

from skimage import filters, morphology, measure
from skimage.filters import gaussian
from skimage.color import label2rgb
from matplotlib import pyplot as plt
from microfilm.microplot import microshow

## Getting Credentials and connecting to OMERO

In [ ]:
OMEROUSER = ""
OMEROPASS = getpass.getpass(prompt = f"Enter password: \t")

OMEROHOST = ""
OMEROPORT = "4064"


In [ ]:
# Connection Check:
conn=ezomero.connect(OMEROUSER, OMEROPASS, host=OMEROHOST, port=OMEROPORT, secure=False)

## Information about the connection and its status
print(conn.isConnected())
user = conn.getUser()
print("Current user:")
print("   ID:", user.getId())
print("   Username:", user.getName())
print("   Full Name:", user.getFullName())

## Retrieving an image

In [ ]:
img_id = 000000 # 2D 2 channel image, nuclei to segment in the first channel = 0

In [ ]:
img = conn.getObject("Image", img_id)

In [ ]:
pixels = img.getPrimaryPixels()
print(img.getName(), img.getDescription())
# Retrieve information about an image.
print (" X:", img.getSizeX())
print (" Y:", img.getSizeY())
print (" Z:", img.getSizeZ())
print (" C:", img.getSizeC())
print (" T:", img.getSizeT())
# List Channels (loads the Rendering settings to get channel colors)
for channel in img.getChannels():
    print ('Channel:', channel.getLabel(),)
    print ('Color:', channel.getColor().getRGB())
    print ('Lookup table:', channel.getLut())

In [ ]:
## get nuclei (channel 0) and cytoplasm (channel 1)
nuclei = pixels.getPlane(0, 0, 0) 
cyto = pixels.getPlane(0, 1, 0) 

In [ ]:
## recreate the original image
multi_channel_image = np.dstack((nuclei, cyto))
original_image = multi_channel_image.transpose((2, 0, 1))

fig, axs = plt.subplots(1,3, figsize=(20,20))
microshow(original_image, ax=axs[0], label_text= f'{img.getName()}', label_font_size=10, label_color='white')
microshow(nuclei, ax=axs[1], label_text=f'{img.getName()} - Nuclei', label_font_size=10, label_color='white')
microshow(cyto, ax=axs[2], label_text=f'{img.getName()} - Cytoplasm', label_font_size=10, label_color='white')

## Performing a simple segmentation

In [ ]:
# create a square with width and height = 5
square = morphology.footprint_rectangle((3,3)) 
square

threshold = filters.threshold_otsu(nuclei)
binary_image = nuclei >= threshold
opened = morphology.binary_opening(binary_image, square)
labeled_blobs = measure.label(opened)
cleaned = morphology.remove_small_objects(labeled_blobs, min_size=5)

In [ ]:
fig, axs = plt.subplots(2,2, figsize=(15,15))
microshow(nuclei, ax=axs[0,0], label_text='Nuclei', label_color='white')
microshow(opened, ax=axs[0,1], label_text='Binary', label_color='white')
microshow(cleaned, ax=axs[1,0], label_text='Labels', label_color='white')
microshow(original_image, ax=axs[1,1], label_text='Original', label_color='white')

In [ ]:
image_label_overlay = label2rgb(cleaned, image=nuclei, bg_label=0)

fig, ax = plt.subplots(figsize=(10, 10))
ax.imshow(image_label_overlay)

## Sending ROIs to OMERO

In [ ]:
updateService = conn.getUpdateService()

def create_roi(img, shapes):
    roi = omero.model.RoiI()
    roi.setImage(img._obj)
    for shape in shapes:
        roi.addShape(shape)
    updateService.saveObject(roi)

mask = omero_rois.masks_from_label_image(cleaned, rgba=(0, 255, 255, 255), z=0, c=0, t=0,
                                                     text="Labelling Masks", raise_on_no_mask=False)
create_roi(img, mask)

## Measuring cell areas and intensities, and posting the table to OMERO

In [ ]:
table = measure.regionprops_table(cleaned, multi_channel_image, properties=("label", "area", "intensity_mean"))
table = pd.DataFrame(table)
table

In [ ]:
ezomero.post_table(conn=conn, table=table, object_type="Image", object_id=img_id, title="cell_measures")
